# Contents
- [Introduction]()
- [Testset generation]()
- [Build RAG with llama-index]()
- [Tracing using Phoenix]()
- [Evaluation]()
- [Embedding analysis]()
- [Conclusion]()

TODO

- Launch Phoenix.
- Index corpus.
- Transform embedding spans into a corpus (including node IDs).
- Relaunch Phoenix.
- Instrument LlamaIndex.
- Run LlamaIndex application.
- Look at UI, understand traces.
- Export and flatten span data into a phoenix dataset.
- Save to disk.
- Restart Phoenix.
- Instrument LangChain.
- Run evaluations.
- Show evaluations.
- Close Phoenix.
- Load saved trace data into `px.TraceDataset`.
- Map root span IDs over Ragas evaluations, create `SpanEvaluations`, used `add_evaluations` API to attach evaluations to trace dataset and launch Phoenix with that trace dataset.
- User gets to see their annotated applications spans.
- Display traces with annotated evaluations.
- Export using the query DSL to get a primary dataset for visualizing embeddings. Alternatively, call `get_spans_dataframe` on trace `px.TraceDataset`. Whichever is simpler.
- Wrangle out the corpus dataset from LlamaIndex in-memory vector store.
- Re-launch Phoenix with primary and corpus datasets.

## Introduction

In this notebook

In [ ]:
!pip install ragas pypdf arize-phoenix llama-index pandas

In [1]:
import pandas as pd

# Display the complete contents of dataframe cells.
pd.set_option("display.max_colwidth", None)

## Synthetic Test data generation

Follow the instructions [here](https://docs.github.com/en/repositories/working-with-files/managing-large-files/installing-git-large-file-storage) to install `git-lfs`.

In [ ]:
! git lfs install
! git clone https://huggingface.co/datasets/explodinggradients/prompt-engineering-papers

In [2]:
from llama_index import SimpleDirectoryReader

In [3]:
dir_path = "./prompt-engineering-papers"
reader = SimpleDirectoryReader(dir_path, num_files_limit=2)
documents = reader.load_data()

In [4]:
from ragas.testset.generator import TestsetGenerator
from ragas.testset.evolutions import simple, reasoning, multi_context

# generator with openai models
generator = TestsetGenerator.with_openai()

# set question type distribution
distribution = {simple: 0.5, reasoning: 0.25, multi_context: 0.25}

# generate testset
testset = generator.generate_with_llamaindex_docs(
    documents, test_size=10, distributions=distribution
)

embedding nodes:   0%|          | 0/222 [00:00<?, ?it/s]

Generating:   0%|          | 0/10 [00:00<?, ?it/s]

max retries exceeded for ReasoningEvolution(generator_llm=LangchainLLMWrapper(run_config=RunConfig(timeout=60, max_retries=15, max_wait=90, exception_types=<class 'openai.RateLimitError'>)), docstore=InMemoryDocumentStore(splitter=<langchain.text_splitter.TokenTextSplitter object at 0x29da905b0>, nodes=[Node(page_content='arXiv:1605.08386v1  [math.CO]  26 May 2016HEAT-BATH RANDOM WALKS WITH MARKOV BASES\nCAPRICE STANLEY AND TOBIAS WINDISCH\nAbstract. Graphs on lattice points are studied whose edges come from a ﬁ nite set of\nallowed moves of arbitrary length. We show that the diameter of these graphs on ﬁbers of a\nﬁxed integer matrix can be bounded from above by a constant. W e then study the mixing\nbehaviour of heat-bath random walks on these graphs. We also state explicit conditions\non the set of moves so that the heat-bath random walk, a genera lization of the Glauber\ndynamics, is an expander in ﬁxed dimension.\nContents\n1. Introduction 1\n2. Graphs and statistics 3\n3. Bounds 

In [5]:
test_df = testset.to_pandas()
test_df.to_csv("ragas_testdata.csv")
test_df.head()

question  \
0               What is the relationship between the lattice width of F and the diameter of F(M) according to Lemma 3.1?   
1                    What are some strategies proposed to enhance the in-context learning capability of language models?   
2            How do Transformers utilize implicit empirical risk minimization to enhance their task recognition ability?   
3                                    What is the relationship between Markov bases and the mixing time of a random walk?   
4  How does the theory of general relativity explain the inability of anything, including light, to escape a black hole?   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    contexts  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      

## Build RAG with llama-index

In [6]:
import phoenix as px

session = px.launch_app()

🌍 To view the Phoenix app in your browser, visit http://localhost:6006/
📺 To view the Phoenix app in a notebook, run `px.active_session().view()`
📖 For more information on how to use Phoenix, check out https://docs.arize.com/phoenix


In [7]:
import llama_index

llama_index.set_global_handler("arize_phoenix")

In [8]:
import nest_asyncio
from llama_index import VectorStoreIndex, ServiceContext
from llama_index.embeddings import OpenAIEmbedding
from datasets import Dataset

nest_asyncio.apply()


def build_query_engine(documents):
    vector_index = VectorStoreIndex.from_documents(
        documents,
        service_context=ServiceContext.from_defaults(chunk_size=512),
        embed_model=OpenAIEmbedding(),
    )

    query_engine = vector_index.as_query_engine(similarity_top_k=2)
    return query_engine


def generate_response(query_engine, question):
    response = query_engine.query(question)
    return {
        "answer": response.response,
        "contexts": [c.node.get_content() for c in response.source_nodes],
    }


# Function to evaluate as Llama index does not support async evaluation for HFInference API
def generate_ragas_dataset(query_engine, test_df):
    test_questions = test_df["question"].values
    responses = [generate_response(query_engine, q) for q in test_questions]

    dataset_dict = {
        "question": test_questions,
        "answer": [response["answer"] for response in responses],
        "contexts": [response["contexts"] for response in responses],
        "ground_truth": test_df["ground_truth"].values.tolist(),
    }
    ds = Dataset.from_dict(dataset_dict)
    return ds

In [ ]:
generate_response(query_engine, test_df["question"][1])

In [ ]:
query_engine = build_query_engine(documents)
ragas_eval_dataset = generate_responses(query_engine, test_df)

![](../../_static/imgs/arize-tracing1.gif)

In [ ]:
ragas_eval_dataset

## Evaluation

In [ ]:
from ragas import evaluate
from ragas.metrics import (
    faithfulness,
    answer_correctness,
    context_recall,
    context_precision,
)

In [ ]:
from phoenix.trace.langchain import OpenInferenceTracer

tracer = OpenInferenceTracer()

In [ ]:
ragas_scores = evaluate(
    dataset=ragas_eval_dataset,
    metrics=[faithfulness, answer_correctness, context_recall, context_precision],
    callbacks=[tracer],
)

In [ ]:
ragas_scores

![](../../_static/imgs/arize-tracing2.gif)

## Embedding analysis
TBD:
- cluster queries
- color each data point based on question type?
- display average score for each cluster